In [0]:
import numpy as np
import sklearn.datasets

%matplotlib inline
import matplotlib.pyplot as plt

# X: 200 by 2, each row is an (x, y) position
# y: 200 by 1, each entry is the label (0 for red, 1 for blue)
X,y = sklearn.datasets.make_moons(200,noise=0.2) 

plt.scatter(X[:,0],X[:,1],s=40,c=y,cmap=plt.cm.Spectral)



In [0]:
# Code for visualizations - feel free to ignore this:

def plot_classifier(cls, ax, X, y, W, b):
  # Ax+By+C = 0
  A, B = W[cls,:] 
  C = b[cls]

  # Solve for the y coord at the left and right sides of the plot:
  # y = (-C - Ax) / B
  xleft, xright = X[:,0].min(), X[:,0].max()
  yleft = (-C - A*xleft) / B
  yright = (-C - A*xright) / B 
  colors = ['b', 'g']
  
  # plot the classifier line:
  ax.plot([xleft, xright], [yleft, yright], colors[cls])

def visualize(model, output, loss):
    """ visualize the current classifier and its performance on the training data """
    # get predictions
    preds = np.argmax(output.detach().numpy(), axis=1) 

    # calculate accuracy
    correct = np.sum(preds == y)
    vis = preds.astype(np.float32)
    vis[preds != y] = 0.5 # incorrect points get visualized as in-between
    
    # plot predictions vs ground truth
    fig, ax = plt.subplots(1,2)
    fig.suptitle(f"Loss: {loss.item()} Accuracy: {correct / y.shape[0]}")
    
    ax[0].scatter(X[:,0],X[:,1],s=40,c=y,cmap=plt.cm.winter) # original dataset
    ax[1].scatter(X[:,0],X[:,1],s=40,c=vis,cmap=plt.cm.winter) # color-coded predictions
    plot_classifier(0, ax[1], X, y, model.W, model.b) # draw "blue" classifier line
    plot_classifier(1, ax[1], X, y, model.W, model.b) # draw "green" classifier line
    ax[1].set_xlim(*ax[0].get_xlim())
    ax[1].set_ylim(*ax[0].get_ylim())
    plt.show()


In [0]:
import torch
import torch.nn as nn
import torch.nn.functional as F


# Model definition:
class LinearClassifier(nn.Module):
    def __init__(self):
        super(LinearClassifier, self).__init__()

        # 1 input image channel, 6 output channels, 5x5 square convolution
        # kernel
        # randomly initialize 2 classifiers:
        self.W = torch.randn(2, 2, dtype=torch.float, requires_grad=True)
        self.b = torch.randn(2, 1, dtype=torch.float, requires_grad=True)

    def forward(self, x):
        """ Evaluates the classifier on an input x """
        scores = (torch.mm(self.W, x.T) + self.b).T
        return F.softmax(scores, dim=1)

    def loss(self, probs, ytrue):
        """ Calculate cross-entropy loss """
        return F.cross_entropy(probs, ytrue)

    def update(self):
      """ Pre: backward() has been called """
      with torch.no_grad():
        self.W -= lr * self.W.grad
        self.b -= lr * self.b.grad

    def zero_grads(self):
      # zero out the gradients
      self.W.grad.zero_()
      self.b.grad.zero_()

# Make X and y into torch tensors that the model can compute on
Xtensor = torch.from_numpy(X.astype(np.float32))
ytensor = torch.from_numpy(y)




In [0]:
#


# training loop
model = LinearClassifier()
lr = 0.5 # step size (learning rate)
epochs = 50 # number of passes through the entire dataset

for i in range(epochs):
  # make predictions:
  output = model.forward(Xtensor)

  # calculate the loss
  loss = model.loss(output, ytensor)

  # calculate gradients of the loss wrt all input Variables;
  # gradients are stored in each Variable's `.grad` field.
  loss.backward()

  # turn off gradient tracking while we do a parameter update:
  with torch.no_grad():

    model.update() # update model parameters

    visualize(model, output, loss) # plot stuff

  model.zero_grads() # zero out the gradient storage for the next round

